# Expression indicators: MFE, gtai, Ew, DCBS, ENC'


## Input

csv with at least "Entry" and "mut_CDS" column

In [12]:
input_csv = "pet2025_ZS_list_withCDS.csv"
name_seq_set = "Muts"

In [ ]:
# make fasta
import pandas as pd

df = pd.read_csv(input_csv)
with open(f"{name_seq_set}_seqs.fasta", "w") as f:
    for i, row in df.iterrows():
        f.write(f">{row['Entry']}\n{row['mut_CDS']}\n")

## 1. MFE - Minimal free energy from Viennafold

In [4]:
import RNA
print(RNA.__version__)
RNA.params_load_RNA_Turner2004()


def mfe_viennarna(seq: str) -> float:
    seq = seq.strip().upper().replace("T", "U")
    md = RNA.md()
    md.temperature = 37.0

    fc = RNA.fold_compound(seq)
    structure, mfe = fc.mfe()
    return float(mfe)

2.7.0


In [5]:
# predict sequences - can take a while
cds = df["mut_CDS"].to_list()

mfe_results = []
for seq in cds:
    mfe = mfe_viennarna(seq)
    mfe_results.append(mfe)

df["MFE_ViennaRNA"] = mfe_results

In [ ]:
df.to_csv(f"{name_seq_set}_mfe.csv", index=False)

## 2. gTAI - Genetic tRNA Adaptation Index

gtai: https://github.com/AliYoussef96/gtAI

values from 0 to 1

higher values mean that more codons in the gene are adapted to the (species dependent) tRNA pool

copied the following function from their github and removed

    if "gtrnadb.ucsc.edu" not in url:

            raise ValueError ("url is not includes in GtRNAdb database")


-> this url is not up to date anymore, but when the block is removed, it does extract data from webpage

In [7]:

def GtRNAdb(url):
    """
        Get the tRNA genes count from GtRNAdb database
    Args:
        url (string): a url to anticodon table for organism from GtRNAdb database (http://gtrnadb.ucsc.edu/)
    Returns:
        A dictionary of each anticodon and its gene count  
    Raises:
        ValueError if the URL, not a valid for GtRNAdb database
    Example:

        #example 1

        > GtRNAdb("http://gtrnadb.ucsc.edu/genomes/eukaryota/Hsapi19/")
      
    """

    amino_acid_list = ['Val', 'Ile', 'Leu', 'Glu', 'Gln', 'Asp', 'Asn', 'His', 'Trp', 'Phe', 'Tyr', 'Arg', 'Lys', 'Ser', 'Thr', 'Met', 'Ala', 'Gly', 'Pro', 'Cys']

    for start_from_table in range(1,4):

        tables = pd.read_html(url)
        anti_codon_dict = {}

        def SPLIT(x):
            return x.split(" ")

        A_to_I_anticodon = ["AGA","AAG","AGG","ACG","AAU","AGU","AAC","AGC","ACC"]  #codons which will convert its A to I in Wobble pos.
        cat_anti_codon = ()
        for i in range(start_from_table,len(tables)):
            tables_new = tables[i]
        
            for j in range(0, len(tables_new.index)):
                overview = tables_new.iloc[j,1:] 
                codon_anticodon = list ( map(str, overview) )    
                codon_anticodon = list ( map(SPLIT, codon_anticodon) ) 
                
                #anti_codon with A that will convert to I
                for i_codon in codon_anticodon:
                    if not i_codon[0].isdigit() and i_codon[0] != "&nbsp":
                        i_codon_rna = i_codon[0].replace("T","U")
                        if i_codon_rna in A_to_I_anticodon:
                            i_codon_rna = list(i_codon_rna)
                            i_codon_rna[0] = "I"
                            i_codon_rna = "".join(i_codon_rna)

                        try:
                            if i_codon_rna == "CAU" and "/" in i_codon[1]:
                                cat_anti_codon = cat_anti_codon + ( i_codon[1].split("/")[0] , )
                                cat_anti_codon = cat_anti_codon + ( i_codon[1].split("/")[1] , )
                            if i_codon_rna == "CAU" and "/" not in i_codon[1]:
                                cat_anti_codon = cat_anti_codon + ( i_codon[1] ,)
                            
                            
                            
                            anti_codon_dict[i_codon_rna] = int(i_codon[1])

                        except:
                            anti_codon_dict[i_codon_rna] = 0

        def seeifnumber(x):
            # take list and return a tuble with only number element
            result = ()
            for i in x:
                try:
                    int(i)
                    result = result + (int(i),)
                except:
                    pass
            return (result)


        try:
            anti_codon_dict["CAU"] = sum(seeifnumber(cat_anti_codon))
        except:
            pass

        dict_anti_codons = {}
        
        #remove anti_codons with A in the first postion # caz it not recognize ani codon
        for i_anticodon in list(anti_codon_dict.keys()):
            if i_anticodon[0] == "A":
                del anti_codon_dict[i_anticodon]

        if len(anti_codon_dict) == 0:
            raise ValueError ("No tables were found in this URL")
        else:
            see = sum([1 for i in amino_acid_list if i in anti_codon_dict])
            if see == 0:           
                 #if len(anti_codon_dict) == 58 or len(anti_codon_dict) == 57:
                return anti_codon_dict
                break
            else:
                pass

In [8]:
url = "https://gtrnadb.org/genomes/bacteria/Esch_coli_K_12_MG1655/"
GtRNA = GtRNAdb(url)

In [13]:
#run gtAI
from gtAI import Run_gtAI

genetic_code_number = 11  # prokaryotes
size_pop = 60
generation_number = 100
ref_fasta = ""

main_fasta = f"{name_seq_set}_seqs.fasta"
df_tai , final_dict_wi, rel_values = Run_gtAI.gtai_analysis(main_fasta = main_fasta,GtRNA = GtRNA , ref_fasta = ref_fasta, genetic_code_number = genetic_code_number,size_pop=size_pop, generation_number=generation_number, bacteria=True)
                                        

read fasta
extract codon counts
finished writing
gaft.ConsoleOutput   INFO     Generation number: 100 Population number: 60
gaft.ConsoleOutput   INFO     Generation: 1, best fitness: 0.543, scaled fitness: 0.543
gaft.ConsoleOutput   INFO     Generation: 2, best fitness: 0.543, scaled fitness: 0.543


c:\Users\funke\miniforge3\envs\datanalysis\Lib\site-packages\gtAI\bygaft.py:51: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  corr = float(RSCU_wai_corr["Wi"][0])
c:\Users\funke\miniforge3\envs\datanalysis\Lib\site-packages\gtAI\bygaft.py:51: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  corr = float(RSCU_wai_corr["Wi"][0])
c:\Users\funke\miniforge3\envs\datanalysis\Lib\site-packages\gtAI\bygaft.py:51: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `s

gaft.ConsoleOutput   INFO     Generation: 3, best fitness: 0.543, scaled fitness: 0.543
gaft.ConsoleOutput   INFO     Generation: 4, best fitness: 0.543, scaled fitness: 0.543
gaft.ConsoleOutput   INFO     Generation: 5, best fitness: 0.543, scaled fitness: 0.543


c:\Users\funke\miniforge3\envs\datanalysis\Lib\site-packages\gtAI\bygaft.py:51: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  corr = float(RSCU_wai_corr["Wi"][0])
c:\Users\funke\miniforge3\envs\datanalysis\Lib\site-packages\gtAI\bygaft.py:51: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  corr = float(RSCU_wai_corr["Wi"][0])
c:\Users\funke\miniforge3\envs\datanalysis\Lib\site-packages\gtAI\bygaft.py:51: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `s

gaft.ConsoleOutput   INFO     Generation: 6, best fitness: 0.543, scaled fitness: 0.543
gaft.ConsoleOutput   INFO     Generation: 7, best fitness: 0.543, scaled fitness: 0.543
gaft.ConsoleOutput   INFO     Generation: 8, best fitness: 0.543, scaled fitness: 0.543
gaft.ConsoleOutput   INFO     Generation: 9, best fitness: 0.543, scaled fitness: 0.543


...

c:\Users\funke\miniforge3\envs\datanalysis\Lib\site-packages\gtAI\bygaft.py:51: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  corr = float(RSCU_wai_corr["Wi"][0])
c:\Users\funke\miniforge3\envs\datanalysis\Lib\site-packages\gtAI\bygaft.py:51: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  corr = float(RSCU_wai_corr["Wi"][0])
c:\Users\funke\miniforge3\envs\datanalysis\Lib\site-packages\gtAI\bygaft.py:51: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `s

gaft.ConsoleOutput   INFO     Generation: 94, best fitness: 0.551, scaled fitness: 0.551
gaft.ConsoleOutput   INFO     Generation: 95, best fitness: 0.551, scaled fitness: 0.551
gaft.ConsoleOutput   INFO     Generation: 96, best fitness: 0.551, scaled fitness: 0.551
gaft.ConsoleOutput   INFO     Generation: 97, best fitness: 0.551, scaled fitness: 0.551


c:\Users\funke\miniforge3\envs\datanalysis\Lib\site-packages\gtAI\bygaft.py:51: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  corr = float(RSCU_wai_corr["Wi"][0])
c:\Users\funke\miniforge3\envs\datanalysis\Lib\site-packages\gtAI\bygaft.py:51: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  corr = float(RSCU_wai_corr["Wi"][0])
c:\Users\funke\miniforge3\envs\datanalysis\Lib\site-packages\gtAI\bygaft.py:51: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `s

gaft.ConsoleOutput   INFO     Generation: 98, best fitness: 0.551, scaled fitness: 0.551
gaft.ConsoleOutput   INFO     Generation: 99, best fitness: 0.551, scaled fitness: 0.551
gaft.ConsoleOutput   INFO     Generation: 100, best fitness: 0.551, scaled fitness: 0.551
gaft.ConsoleOutput   INFO     Optimal solution: ([0.017578125, 0.482421875, 0.87109375, 0.32421875, 0.896484375], 0.5509850124932588)
gaft.FitnessStore   INFO     Best fitness values are written to best_fit.py


c:\Users\funke\miniforge3\envs\datanalysis\Lib\site-packages\gtAI\bygaft.py:51: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  corr = float(RSCU_wai_corr["Wi"][0])
c:\Users\funke\miniforge3\envs\datanalysis\Lib\site-packages\gtAI\bygaft.py:51: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  corr = float(RSCU_wai_corr["Wi"][0])
c:\Users\funke\miniforge3\envs\datanalysis\Lib\site-packages\gtAI\bygaft.py:51: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `s

In [14]:
df_tai

id       tai
0     001BL2  0.302266
1     001HP1  0.301442
2     001NT0  0.302703
3     001TWZ  0.303060
4     00200Y  0.302229
...      ...       ...
4983  0NJ3EN  0.290563
4984  0NJ9IM  0.310411
4985  0NJFML  0.307290
4986  0NJLQK  0.301183
4987  0NJRUJ  0.308687

[4988 rows x 2 columns]

In [15]:
max_tai = max(df_tai["tai"])
min_tai = min(df_tai["tai"])
print("max tai:", max_tai)
print("min tai", min_tai)

max tai: 0.3302979040884349
min tai 0.27974645719284663


In [28]:
df_mfe_tai = df.join(df_tai["tai"])

df_mfe_tai

Unnamed: 0   Entry mutation  \
0              0  001BL2     V26A   
1              1  001HP1     V26C   
2              2  001NT0     V26D   
3              3  001TWZ     V26E   
4              4  00200Y     V26F   
...          ...     ...      ...   
4985        4985  0NJ3EN       wt   
4986        4986  0NJ9IM       wt   
4987        4987  0NJFML       wt   
4988        4988  0NJLQK       wt   
4989        4989  0NJRUJ       wt   

                                               Sequence  wt_idx  \
0     AADNPYQRGPDPTNASIEAATGPFAAGTQPIVGASGFGGGQIYYPT...       0   
1     AADNPYQRGPDPTNASIEAATGPFACGTQPIVGASGFGGGQIYYPT...       0   
2     AADNPYQRGPDPTNASIEAATGPFADGTQPIVGASGFGGGQIYYPT...       0   
3     AADNPYQRGPDPTNASIEAATGPFAEGTQPIVGASGFGGGQIYYPT...       0   
4     AADNPYQRGPDPTNASIEAATGPFAFGTQPIVGASGFGGGQIYYPT...       0   
...                                                 ...     ...   
4985  SNITGNGSFSVSTYNISSLVTGFGGGVAYYPSTAGRYPVVAVSPGF...     308   
4986  ASLKSRSGPFNVDRFSVSGYLKGFGDSTVYYPTNATGKMGAIAVIP...     309   
4987  MGVRYPEQGGFGGVAAVPGYNSAEKAVAWLGPRLASQGFVVITIAT...     310   
4988  RALLEAPRGPLATARTVVPRAEAAGYGGGTIYHPAEMRTGETYGAV...     311   
4989  SVRAQQGPFTTDKLVVPAQAGRGFNKGTIYYPDDTSQGTFGAVAVI...     312   

                                         wt_aa_sequence  \
0     AADNPYQRGPDPTNASIEAATGPFAVGTQPIVGASGFGGGQIYYPT...   
1     AADNPYQRGPDPTNASIEAATGPFAVGTQPIVGASGFGGGQIYYPT...   
2     AADNPYQRGPDPTNASIEAATGPFAVGTQPIVGASGFGGGQIYYPT...   
3     AADNPYQRGPDPTNASIEAATGPFAVGTQPIVGASGFGGGQIYYPT...   
4     AADNPYQRGPDPTNASIEAATGPFAVGTQPIVGASGFGGGQIYYPT...   
...                                                 ...   
4985  SNITGNGSFSVSTYNISSLVTGFGGGVAYYPSTAGRYPVVAVSPGF...   
4986  ASLKSRSGPFNVDRFSVSGYLKGFGDSTVYYPTNATGKMGAIAVIP...   
4987  MGVRYPEQGGFGGVAAVPGYNSAEKAVAWLGPRLASQGFVVITIAT...   
4988  RALLEAPRGPLATARTVVPRAEAAGYGGGTIYHPAEMRTGETYGAV...   
4989  SVRAQQGPFTTDKLVVPAQAGRGFNKGTIYYPDDTSQGTFGAVAVI...   

                                                 wt_CDS  \
0     GCTGCAGATAATCCATATCAAAGGGGACCCGACCCGACGAACGCCT...   
1     GCTGCAGATAATCCATATCAAAGGGGACCCGACCCGACGAACGCCT...   
2     GCTGCAGATAATCCATATCAAAGGGGACCCGACCCGACGAACGCCT...   
3     GCTGCAGATAATCCATATCAAAGGGGACCCGACCCGACGAACGCCT...   
4     GCTGCAGATAATCCATATCAAAGGGGACCCGACCCGACGAACGCCT...   
...                                                 ...   
4985  TCAAATATAACAGGAAACGGGTCTTTTAGTGTCAGCACCTATAACA...   
4986  GCTTCACTAAAAAGTAGGTCTGGACCCTTTAACGTCGATCGTTTCA...   
4987  ATGGGAGTAAGGTATCCCGAACAAGGTGGGTTCGGCGGGGTGGCCG...   
4988  AGGGCTCTATTAGAAGCACCAAGAGGACCCTTGGCCACCGCACGCA...   
4989  TCAGTAAGGGCTCAGCAAGGACCCTTTACAACTGACAAATTGGTTG...   

                                                mut_CDS  mutation_valid  \
0     GCTGCAGATAATCCATATCAAAGGGGACCCGACCCGACGAACGCCT...            True   
1     GCTGCAGATAATCCATATCAAAGGGGACCCGACCCGACGAACGCCT...            True   
2     GCTGCAGATAATCCATATCAAAGGGGACCCGACCCGACGAACGCCT...            True   
3     GCTGCAGATAATCCATATCAAAGGGGACCCGACCCGACGAACGCCT...            True   
4     GCTGCAGATAATCCATATCAAAGGGGACCCGACCCGACGAACGCCT...            True   
...                                                 ...             ...   
4985  TCAAATATAACAGGAAACGGGTCTTTTAGTGTCAGCACCTATAACA...            True   
4986  GCTTCACTAAAAAGTAGGTCTGGACCCTTTAACGTCGATCGTTTCA...            True   
4987  ATGGGAGTAAGGTATCCCGAACAAGGTGGGTTCGGCGGGGTGGCCG...            True   
4988  AGGGCTCTATTAGAAGCACCAAGAGGACCCTTGGCCACCGCACGCA...            True   
4989  TCAGTAAGGGCTCAGCAAGGACCCTTTACAACTGACAAATTGGTTG...            True   

            mutation_log mut_codon  MFE_ViennaRNA       tai  
0                Success       GCG    -309.000000  0.302266  
1                Success       TGC    -306.299988  0.301442  
2                Success       GAT    -309.700012  0.302703  
3                Success       GAA    -313.500000  0.303060  
4                Success       TTT    -306.299988  0.302229  
...                  ...       ...            ...       ...  
498

In [17]:
#df_tai.to_csv(f"{name_seq_set}_mfe_tai.csv", index=False)

In [18]:
#df_mfe_tai.iloc[0:2]
#genescript: id1 tai: 0.21 and gtai:0.25
#id2 tai:0.22 and gtai:0.26

## 3. Ew - weighted sum of relative entropy
paper: https://www.sciencedirect.com/science/article/pii/S0378111904001477?via%3Dihub

between 0 and 1  

higher values mean there is less codon usage bias

In [29]:
from __future__ import annotations

import math
from dataclasses import dataclass
from typing import Dict, List, Tuple, Optional


# Standard genetic code (DNA codons)
CODON_TO_AA: Dict[str, str] = {
    # Phenylalanine / Leucine
    "TTT":"F","TTC":"F","TTA":"L","TTG":"L",
    "CTT":"L","CTC":"L","CTA":"L","CTG":"L",
    # Isoleucine / Methionine
    "ATT":"I","ATC":"I","ATA":"I","ATG":"M",
    # Valine
    "GTT":"V","GTC":"V","GTA":"V","GTG":"V",
    # Serine / Proline / Threonine / Alanine
    "TCT":"S","TCC":"S","TCA":"S","TCG":"S",
    "CCT":"P","CCC":"P","CCA":"P","CCG":"P",
    "ACT":"T","ACC":"T","ACA":"T","ACG":"T",
    "GCT":"A","GCC":"A","GCA":"A","GCG":"A",
    # Tyrosine / Stop / Histidine / Glutamine
    "TAT":"Y","TAC":"Y","TAA":"*","TAG":"*",
    "CAT":"H","CAC":"H","CAA":"Q","CAG":"Q",
    # Asparagine / Lysine
    "AAT":"N","AAC":"N","AAA":"K","AAG":"K",
    # Aspartate / Glutamate
    "GAT":"D","GAC":"D","GAA":"E","GAG":"E",
    # Cysteine / Stop / Tryptophan
    "TGT":"C","TGC":"C","TGA":"*","TGG":"W",
    # Arginine
    "CGT":"R","CGC":"R","CGA":"R","CGG":"R",
    "AGA":"R","AGG":"R",
    # Serine / Glycine
    "AGT":"S","AGC":"S",
    "GGT":"G","GGC":"G","GGA":"G","GGG":"G",
}

def _build_aa_to_codons(codon_to_aa: Dict[str, str]) -> Dict[str, List[str]]:
    aa_to_codons: Dict[str, List[str]] = {}
    for codon, aa in codon_to_aa.items():
        if aa == "*":
            continue
        aa_to_codons.setdefault(aa, []).append(codon)
    # stable ordering (optional)
    for aa in aa_to_codons:
        aa_to_codons[aa].sort()
    return aa_to_codons

AA_TO_CODONS = _build_aa_to_codons(CODON_TO_AA)

@dataclass(frozen=True)
class EwResult:
    ew: float
    per_aa_Ei: Dict[str, float]
    per_aa_wi: Dict[str, float]
    per_aa_Hi: Dict[str, float]
    included_aa_counts: Dict[str, int]


def compute_ew(
    dna_seq: str,
    *,
    ignore_trailing: bool = True,
    log_base: Optional[float] = 2,  # 2 => log2
) -> EwResult:
    """
    Compute Weighted Sum of Relative Entropy (Ew) for a coding DNA sequence.

    Definitions 
      Hi  = -sum_j p_ij * log2(p_ij) -> p_ij: i is aa, j is codon -> how many are codon j out of all codons for aa i
      Hi_max = log2(k_i)  -> k_i is codon degeneracy for amino acid i
      Ei = Hi / Hi_max 
      wi = (sum_j x_ij) / (sum_i sum_j x_ij)  -> how often amino acid i appears in sequence / how many aa in sequence
      Ew = sum_i wi * Ei

    Notes:
      - Excludes Met (M) and Trp (W) by default (degeneracy 1 -> undefined Ei).
      - Stop codons (if) are removed
      - log base does not affect Ei if used consistently in numerator and denominator.
    """
    
    seq = dna_seq.strip().upper().replace("U", "T").replace(" ", "").replace("\n", "").replace("\r", "")
    #seq = seq[3:] # remove start codon
    if seq[-3:] in {"TAA", "TAG", "TGA"}:
        seq = seq[:-3]  # remove stop codon if there
    
    if len(seq) % 3 != 0:
        raise ValueError("CDS length must be divisible by 3")

    # codon counts per amino acid, and per codon within amino acid
    codon_counts_by_aa: Dict[str, Dict[str, int]] = {}
    aa_total_counts: Dict[str, int] = {}

    for i in range(0, len(seq), 3):
        codon = seq[i:i+3]
        aa = CODON_TO_AA.get(codon)
        if aa is None:
            ignored_codons += 1
            continue

        codon_counts_by_aa.setdefault(aa, {})
        codon_counts_by_aa[aa][codon] = codon_counts_by_aa[aa].get(codon, 0) + 1
        aa_total_counts[aa] = aa_total_counts.get(aa, 0) + 1

    # Only include amino acids with degeneracy > 1 and present in the sequence
    included_aas: List[str] = []
    for aa, total in aa_total_counts.items():
        k_i = len(AA_TO_CODONS.get(aa, []))
        if total > 0 and k_i > 1:
            included_aas.append(aa)

    if not included_aas:
        return EwResult(ew=float("nan"), per_aa_Ei={}, per_aa_wi={}, per_aa_Hi={},
                        included_aa_counts={}, ignored_codons=ignored_codons)

    def _log(x: float) -> float:
        if log_base is None:
            return math.log(x)
        return math.log(x, log_base)

    # Total counts across all amino acids (for weights)
    total_included = sum(aa_total_counts[aa] for aa in aa_total_counts)

    per_aa_Hi: Dict[str, float] = {}
    per_aa_Ei: Dict[str, float] = {}
    per_aa_wi: Dict[str, float] = {}
    included_counts: Dict[str, int] = {}

    ew = 0.0
    for aa in included_aas:
        counts = codon_counts_by_aa.get(aa, {})
        total = aa_total_counts[aa]
        included_counts[aa] = total

        # probabilities p_ij over observed codons for this aa (unobserved codons have p=0, contribute 0)
        Hi = 0.0
        for codon, c in counts.items():
            p = c / total
            if p > 0:
                Hi += -p * _log(p)

        k_i = len(AA_TO_CODONS[aa])
        Hi_max = _log(k_i)  # = log(k_i)

        # Ei = Hi / Hi_max
        Ei = Hi / Hi_max if Hi_max != 0 else float("nan")

        wi = total / total_included

        per_aa_Hi[aa] = Hi
        per_aa_Ei[aa] = Ei
        per_aa_wi[aa] = wi

        ew += wi * Ei

    # ew should be in [0,1] up to floating error
    ew = max(0.0, min(1.0, ew))

    return EwResult(
        ew=ew,
        per_aa_Ei=per_aa_Ei,
        per_aa_wi=per_aa_wi,
        per_aa_Hi=per_aa_Hi,
        included_aa_counts=included_counts,
    )



In [30]:
ew_scores = []
for seq in df_mfe_tai["mut_CDS"].tolist():
    res = compute_ew(seq)
    ew_scores.append(res.ew)
    print("Ew =", res.ew)
    print("Per-AA Ei =", res.per_aa_Ei)
    print("Per-AA wi =", res.per_aa_wi)

Ew = 0.757932428485624
Per-AA Ei = {'A': 0.8985416133348303, 'D': 1.0, 'N': 0.9940302114769565, 'P': 0.5591375803854881, 'Y': 1.0, 'Q': 0.9910760598382222, 'R': 0.6861056057023637, 'G': 0.6954281491932058, 'T': 0.6889451659416073, 'S': 0.7440029291716864, 'I': 0.6282340759682773, 'E': 0.9709505944546686, 'F': 0.9957274520849256, 'V': 0.8447411335095912, 'L': 0.56929346595908, 'K': 0.9709505944546686, 'H': 1.0, 'C': 1.0}
Per-AA wi = {'A': 0.1274131274131274, 'D': 0.05405405405405406, 'N': 0.04247104247104247, 'P': 0.08108108108108109, 'Y': 0.03088803088803089, 'Q': 0.03474903474903475, 'R': 0.05791505791505792, 'G': 0.09652509652509653, 'T': 0.08108108108108109, 'S': 0.07722007722007722, 'I': 0.05019305019305019, 'E': 0.019305019305019305, 'F': 0.05019305019305019, 'V': 0.05791505791505792, 'L': 0.05791505791505792, 'K': 0.019305019305019305, 'H': 0.007722007722007722, 'C': 0.007722007722007722}
Ew = 0.7587845715963775
Per-AA Ei = {'A': 0.9099278376115947, 'D': 1.0, 'N': 0.9940302114769

In [31]:
df_mfe_tai["ew"] = ew_scores
df_mfe_tai_ew = df_mfe_tai
#df_mfe_tai.to_csv(f"{name_seq_set}_mfe_tai_ew.csv", index=False)

## 4. DCBS  - directional codon Bias score

improvement of RCBS, that includes the positive effect of rare codons
 
higher values indicate stronger codon usage bias

In [32]:
from typing import Dict, List

def compute_dcbs(seqs: List[str], subtract_one: bool = False) -> List[float]:
    out = []

    for seq in seqs:
        L = len(seq) // 3
        if L == 0:
            out.append(0.0)
            continue

        # count codons (only full codons)
        codon_counts: Dict[str, int] = {}
        for i in range(0, 3 * L, 3):
            codon = seq[i:i+3].upper()
            codon_counts[codon] = codon_counts.get(codon, 0) + 1

        # positional nucleotide frequencies f1,f2,f3 (normalized by L)
        f1: Dict[str, float] = {}
        f2: Dict[str, float] = {}
        f3: Dict[str, float] = {}
        for codon, count in codon_counts.items():
            f1[codon[0]] = f1.get(codon[0], 0.0) + count
            f2[codon[1]] = f2.get(codon[1], 0.0) + count
            f3[codon[2]] = f3.get(codon[2], 0.0) + count

        for dct in (f1, f2, f3):
            for b in dct:
                dct[b] /= L

        # DCBS = (1/L) * sum_{i=1..L} d_i
        # compute by codon type, weight by occurrences
        total = 0.0
        for codon, count in codon_counts.items():
            f_xyz = count / L
            prod = f1[codon[0]] * f2[codon[1]] * f3[codon[2]]

            # f_xyz should be >0 here; prod should be >0 as well for valid sequences
            d_xyz = max(f_xyz / prod, prod / f_xyz)
            total += count * d_xyz

        dcbs = total / L
        if subtract_one:
            dcbs -= 1.0  # makes "no bias" closer to 0
        out.append(dcbs)

    return out


In [33]:
dcbs = compute_dcbs(df_mfe_tai["mut_CDS"].tolist())
df_mfe_tai_ew["dcbs"] = dcbs
df_mfe_tai_ew_dcbs = df_mfe_tai_ew
#df_mfe_tai_ew.to_csv(f"{name_seq_set}_mfe_tai_ew_dcbs.csv", index=False)

## 5. ENCprime - effective number of codons

(ENC: evaluates how many codons are used for each amino acid considering its total amount of possible codons.)

ENC prime: effective number of codons in a gene after correcting for expected codon usage derived from background nucleotide composition.

values between 61 (no bias, synonymous usage of codons) to 20 (maximal bias)

go to webapp here: http://agnigarh.tezu.ernet.in/~ssankar/cub.php

paper: https://onlinelibrary.wiley.com/doi/10.1111/gtc.12474


In [34]:
# upload "seqs.fasta" to webapp and get mNc' value

# export resulting txt.file

In [35]:
import pandas as pd


columns = ["Size (aa)", "GC%","GC1%","GC2%","GC3%"," Nc","Nc'","NcFDS","Nc'FDS","Um(g)","Remark"] #if you hit "All" in the webapp

df_enc = pd.read_csv(
    "enc.txt",
    sep=r"\s+",          # split on ANY whitespace (tabs/spaces)
    skiprows=2,          # skip the header line
    comment="-",         # ignore the dashed separator line(s)
    names=columns
)
df_enc

Size (aa)    GC%   GC1%   GC2%   GC3%     Nc    Nc' NcFDS  Nc'FDS  Um(g)  \
0          258  58.82  57.14  55.98  63.32  41.37  43.53     #     NaN    NaN   
1          258  58.69  56.76  55.98  63.32  41.33  43.54     #     NaN    NaN   
2          258  58.56  57.14  55.60  62.93  41.40  43.55     #     NaN    NaN   
3          258  58.56  57.14  55.60  62.93  41.47  43.35     #     NaN    NaN   
4          258  58.43  56.76  55.60  62.93  41.44  43.55     #     NaN    NaN   
..         ...    ...    ...    ...    ...    ...    ...   ...     ...    ...   
879        258  58.43  56.76  55.21  63.32  41.37  43.61     #     NaN    NaN   
880        258  58.82  57.14  55.60  63.71  41.36  43.68     #     NaN    NaN   
881        258  58.56  57.14  55.21  63.32  41.27  43.58     #     NaN    NaN   
882        258  58.43  56.76  55.21  63.32  41.36  43.63     #     NaN    NaN   
883        258  58.43  56.76  55.21  63.32  41.24  43.21   NaN     NaN    NaN   

     Remark  
0       NaN  
1       NaN  
2       NaN  
3       NaN  
4       NaN  
..      ...  
879     NaN  
880     NaN  
881     NaN  
882     NaN  
883     NaN  

[884 rows x 11 columns]

In [36]:
df_all = df_mfe_tai_ew_dcbs.join(df_enc["Nc'"])
df_all

Unnamed: 0   Entry mutation  \
0              0  001BL2     V26A   
1              1  001HP1     V26C   
2              2  001NT0     V26D   
3              3  001TWZ     V26E   
4              4  00200Y     V26F   
...          ...     ...      ...   
4985        4985  0NJ3EN       wt   
4986        4986  0NJ9IM       wt   
4987        4987  0NJFML       wt   
4988        4988  0NJLQK       wt   
4989        4989  0NJRUJ       wt   

                                               Sequence  wt_idx  \
0     AADNPYQRGPDPTNASIEAATGPFAAGTQPIVGASGFGGGQIYYPT...       0   
1     AADNPYQRGPDPTNASIEAATGPFACGTQPIVGASGFGGGQIYYPT...       0   
2     AADNPYQRGPDPTNASIEAATGPFADGTQPIVGASGFGGGQIYYPT...       0   
3     AADNPYQRGPDPTNASIEAATGPFAEGTQPIVGASGFGGGQIYYPT...       0   
4     AADNPYQRGPDPTNASIEAATGPFAFGTQPIVGASGFGGGQIYYPT...       0   
...                                                 ...     ...   
4985  SNITGNGSFSVSTYNISSLVTGFGGGVAYYPSTAGRYPVVAVSPGF...     308   
4986  ASLKSRSGPFNVDRFSVSGYLKGFGDSTVYYPTNATGKMGAIAVIP...     309   
4987  MGVRYPEQGGFGGVAAVPGYNSAEKAVAWLGPRLASQGFVVITIAT...     310   
4988  RALLEAPRGPLATARTVVPRAEAAGYGGGTIYHPAEMRTGETYGAV...     311   
4989  SVRAQQGPFTTDKLVVPAQAGRGFNKGTIYYPDDTSQGTFGAVAVI...     312   

                                         wt_aa_sequence  \
0     AADNPYQRGPDPTNASIEAATGPFAVGTQPIVGASGFGGGQIYYPT...   
1     AADNPYQRGPDPTNASIEAATGPFAVGTQPIVGASGFGGGQIYYPT...   
2     AADNPYQRGPDPTNASIEAATGPFAVGTQPIVGASGFGGGQIYYPT...   
3     AADNPYQRGPDPTNASIEAATGPFAVGTQPIVGASGFGGGQIYYPT...   
4     AADNPYQRGPDPTNASIEAATGPFAVGTQPIVGASGFGGGQIYYPT...   
...                                                 ...   
4985  SNITGNGSFSVSTYNISSLVTGFGGGVAYYPSTAGRYPVVAVSPGF...   
4986  ASLKSRSGPFNVDRFSVSGYLKGFGDSTVYYPTNATGKMGAIAVIP...   
4987  MGVRYPEQGGFGGVAAVPGYNSAEKAVAWLGPRLASQGFVVITIAT...   
4988  RALLEAPRGPLATARTVVPRAEAAGYGGGTIYHPAEMRTGETYGAV...   
4989  SVRAQQGPFTTDKLVVPAQAGRGFNKGTIYYPDDTSQGTFGAVAVI...   

                                                 wt_CDS  \
0     GCTGCAGATAATCCATATCAAAGGGGACCCGACCCGACGAACGCCT...   
1     GCTGCAGATAATCCATATCAAAGGGGACCCGACCCGACGAACGCCT...   
2     GCTGCAGATAATCCATATCAAAGGGGACCCGACCCGACGAACGCCT...   
3     GCTGCAGATAATCCATATCAAAGGGGACCCGACCCGACGAACGCCT...   
4     GCTGCAGATAATCCATATCAAAGGGGACCCGACCCGACGAACGCCT...   
...                                                 ...   
4985  TCAAATATAACAGGAAACGGGTCTTTTAGTGTCAGCACCTATAACA...   
4986  GCTTCACTAAAAAGTAGGTCTGGACCCTTTAACGTCGATCGTTTCA...   
4987  ATGGGAGTAAGGTATCCCGAACAAGGTGGGTTCGGCGGGGTGGCCG...   
4988  AGGGCTCTATTAGAAGCACCAAGAGGACCCTTGGCCACCGCACGCA...   
4989  TCAGTAAGGGCTCAGCAAGGACCCTTTACAACTGACAAATTGGTTG...   

                                                mut_CDS  mutation_valid  \
0     GCTGCAGATAATCCATATCAAAGGGGACCCGACCCGACGAACGCCT...            True   
1     GCTGCAGATAATCCATATCAAAGGGGACCCGACCCGACGAACGCCT...            True   
2     GCTGCAGATAATCCATATCAAAGGGGACCCGACCCGACGAACGCCT...            True   
3     GCTGCAGATAATCCATATCAAAGGGGACCCGACCCGACGAACGCCT...            True   
4     GCTGCAGATAATCCATATCAAAGGGGACCCGACCCGACGAACGCCT...            True   
...                                                 ...             ...   
4985  TCAAATATAACAGGAAACGGGTCTTTTAGTGTCAGCACCTATAACA...            True   
4986  GCTTCACTAAAAAGTAGGTCTGGACCCTTTAACGTCGATCGTTTCA...            True   
4987  ATGGGAGTAAGGTATCCCGAACAAGGTGGGTTCGGCGGGGTGGCCG...            True   
4988  AGGGCTCTATTAGAAGCACCAAGAGGACCCTTGGCCACCGCACGCA...            True   
4989  TCAGTAAGGGCTCAGCAAGGACCCTTTACAACTGACAAATTGGTTG...            True   

            mutation_log mut_codon  MFE_ViennaRNA       tai        ew  \
0                Success       GCG    -309.000000  0.302266  0.757932   
1                Success       TGC    -306.299988  0.301442  0.758785   
2                Success       GAT    -309.700012  0.302703  0.759545   
3                Success       GAA    -313.500000  0.303060  0.760292   
4                Success       TTT    -306.299988  0.302229  0.759945   

In [37]:
df_all.to_csv(f"{name_seq_set}_mfe_tai_ew_dcbs_enc.csv", index=False)